In [ ]:
!pip3 install tinkoff-investments
!pip3 install yfinance
!pip3 install pandas
!pip3 install numpy
!pip3 install decimal
!pip3 install locale

In [38]:
import logging
import os
from datetime import timedelta
from decimal import Decimal


from tinkoff.invest import CandleInterval, Quotation
from tinkoff.invest.retrying.settings import RetryClientSettings
from tinkoff.invest.retrying.sync.client import RetryingClient
from tinkoff.invest.utils import now

logging.basicConfig(format="%(asctime)s %(levelname)s:%(message)s", level=logging.DEBUG)

TOKEN = 't.b7eKSJEp3fpSiiv4mVt4fWwKIxaMHM1lDMtpGsPTeyl850b9Y4MluXYv-EQrj1vEu7QfkNwqGqGPfTW9N6EvTg'

retry_settings = RetryClientSettings(use_retry=True, max_retry_attempt=2)

# Quotation type = MoneyValue. We need to convert this to decimal in order to fetch price per share
def quotation_to_decimal(quotation: Quotation) -> Decimal:
    fractional = quotation.nano / Decimal("10e8")
    return Decimal(quotation.units) + fractional

def get_stock_volumes(_input: int):
    return f'{_input:,} ₽'

def get_final_float_stock_volumes(_input: int):
    return f'{_input:,} ₽'

def get_final_lots(_lots: int):
    return f'{_lots:,} шт.'

def calculate_net_change(current_closing_price: int, prev_closing_price: int):
    return f'Изменение цены: {round(((current_closing_price - prev_closing_price) / prev_closing_price * 100), 2)}%'

def calculate_net_change_per_day(current_closing_price: int, yesterday_closing_price: int):
    # current price minus 840 indexes in order to fetch price index yesterday for 1 minute candle
    return f'Изменение за день: {round(((current_closing_price - yesterday_closing_price) / yesterday_closing_price * 100), 2)}%'

def calculate_net_change_float(current_closing_price: float, prev_closing_price: float):
    return f'Изменение цены: {round(((current_closing_price - prev_closing_price) / prev_closing_price * 100), 2)}%'

def calculate_net_change_per_day_float(current_closing_price: float, yesterday_closing_price: float):
    # current price minus 840 indexes in order to fetch price index yesterday for 1 minute candle
    return f'Изменение за день: {round(((current_closing_price - yesterday_closing_price) / yesterday_closing_price * 100), 2)}%'

def make_million_volumes_on_float_stock_prices(price: int):
    price = str(price)
    price += '0000'
    return int(price)

with RetryingClient(TOKEN, settings=retry_settings) as client:
    l1_volumes = []
    l2_lots = []
    l3_prices = []
    l4_time = []
    data = {"Объем": l1_volumes, "Лоты": l2_lots, "Цена": l3_prices, "Время": l4_time}
    threshold = 8.0
    for candle in client.get_all_candles(
        figi="BBG004730N88",
        from_=now() - timedelta(days=90),
        interval=CandleInterval.CANDLE_INTERVAL_1_MIN,
    ):
         if quotation_to_decimal(candle.close) < 1:
            final_stock_volume_rub = int(candle.volume * float(quotation_to_decimal(candle.close)))
            l1_volumes.append(make_million_volumes_on_float_stock_prices(final_stock_volume_rub))
            l2_lots.append(get_final_lots(candle.volume)) # get_final_lots
            l3_prices.append(float(quotation_to_decimal(candle.close)))
            l4_time.append(candle.time)

            print(f'ВТБ (VTBR), Время: {candle.time}, {get_final_lots(candle.volume)}, {get_final_float_stock_volumes(make_million_volumes_on_float_stock_prices(final_stock_volume_rub))}, Цена: {float(quotation_to_decimal(candle.close))} ₽')
        
         else:
            # BUYING VOLUME AND SELLING VOLUME
            if candle.high == candle.low:
                BV = 0
                SV = 0
            else:
                BV = (float(candle.volume) * (float(quotation_to_decimal(candle.close)) - float(quotation_to_decimal(candle.low)))) / (float(quotation_to_decimal(candle.high)) - float(quotation_to_decimal(candle.low)))
                SV = (float(candle.volume) * (float(quotation_to_decimal(candle.high)) - float(quotation_to_decimal(candle.close)))) / (float(quotation_to_decimal(candle.high)) - float(quotation_to_decimal(candle.low)))
                TP = BV + SV
                print(f'Время: {candle.time}, Цена: {int(quotation_to_decimal(candle.close))} TP = {TP}, Покупка: {round((BV / TP) * 100)}%, Продажа: {round((SV / TP) * 100)}%')


            
            if candle.volume > 0:
                volume = candle.volume
            else:
                volume = 1
            
            '''# RAW Pressure Volume Calculations
            BPV = (BV / TP) * volume
            SPV = (SV / TP) * volume
            TPV = BPV + SPV'''

            final_stock_volume_rub = int(candle.volume * quotation_to_decimal(candle.close))
            l1_volumes.append(final_stock_volume_rub)
            l2_lots.append(get_final_lots(candle.volume)) # get_final_lots
            l3_prices.append(int(quotation_to_decimal(candle.close)))
            l4_time.append(candle.time)
            '''l1_volumes.append(final_stock_volume_rub)
            l2_lots.append(get_final_lots(candle.volume))
            l3_prices.append(int(quotation_to_decimal(candle.close)))
            l4_time.append(candle.time)'''
            #print(f'Яндекс (YNDX), Время: {candle.time}, Покупка: {BPV}, Продажа: {SPV}  {get_final_lots(candle.volume)}, {get_stock_volumes(final_stock_volume_rub)}, Цена: {float(quotation_to_decimal(candle.close))} ₽')
        



2023-05-20 16:13:16,577 DEBUG:Trying to call
2023-05-20 16:13:17,140 DEBUG:Call succeeded
2023-05-20 16:13:17,142 INFO:64689d3dfe94a1d3fe6a41132d964ed6 GetCandles
2023-05-20 16:13:17,193 DEBUG:Trying to call


Время: 2023-02-19 10:13:00+00:00, Цена: 159 TP = 5.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:15:00+00:00, Цена: 159 TP = 12.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:17:00+00:00, Цена: 159 TP = 4.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:18:00+00:00, Цена: 160 TP = 8.0, Покупка: 100%, Продажа: 0%
Время: 2023-02-19 10:19:00+00:00, Цена: 159 TP = 5.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:21:00+00:00, Цена: 160 TP = 14.0, Покупка: 100%, Продажа: 0%
Время: 2023-02-19 10:22:00+00:00, Цена: 159 TP = 66.0, Покупка: 92%, Продажа: 8%
Время: 2023-02-19 10:23:00+00:00, Цена: 159 TP = 9.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:25:00+00:00, Цена: 159 TP = 3.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:26:00+00:00, Цена: 159 TP = 19.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:28:00+00:00, Цена: 160 TP = 380.0, Покупка: 99%, Продажа: 1%
Время: 2023-02-19 10:29:00+00:00, Цена: 159 TP = 12.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-19 10:31

2023-05-20 16:13:17,439 DEBUG:Call succeeded
2023-05-20 16:13:17,439 INFO:64689d3d356247af69807b0377a2a061 GetCandles
2023-05-20 16:13:17,488 DEBUG:Trying to call
2023-05-20 16:13:17,630 DEBUG:Call succeeded
2023-05-20 16:13:17,631 INFO:64689d3d42120655949302ce35289ae7 GetCandles
2023-05-20 16:13:17,682 DEBUG:Trying to call


Время: 2023-02-20 10:14:00+00:00, Цена: 156 TP = 80708.0, Покупка: 0%, Продажа: 100%
Время: 2023-02-20 10:15:00+00:00, Цена: 156 TP = 28252.0, Покупка: 74%, Продажа: 26%
Время: 2023-02-20 10:16:00+00:00, Цена: 156 TP = 7103.0, Покупка: 27%, Продажа: 73%
Время: 2023-02-20 10:17:00+00:00, Цена: 156 TP = 4328.0, Покупка: 75%, Продажа: 25%
Время: 2023-02-20 10:18:00+00:00, Цена: 156 TP = 4905.0, Покупка: 11%, Продажа: 89%
Время: 2023-02-20 10:19:00+00:00, Цена: 156 TP = 18494.0, Покупка: 63%, Продажа: 37%
Время: 2023-02-20 10:20:00+00:00, Цена: 156 TP = 4466.0, Покупка: 75%, Продажа: 25%
Время: 2023-02-20 10:21:00+00:00, Цена: 156 TP = 5232.0, Покупка: 92%, Продажа: 8%
Время: 2023-02-20 10:22:00+00:00, Цена: 156 TP = 4318.0, Покупка: 86%, Продажа: 14%
Время: 2023-02-20 10:23:00+00:00, Цена: 157 TP = 7236.0, Покупка: 77%, Продажа: 23%
Время: 2023-02-20 10:24:00+00:00, Цена: 157 TP = 3959.0, Покупка: 20%, Продажа: 80%
Время: 2023-02-20 10:25:00+00:00, Цена: 156 TP = 2043.0, Покупка: 44%, Про

2023-05-20 16:13:17,830 DEBUG:Call succeeded
2023-05-20 16:13:17,830 INFO:64689d3df012a514220cbc9ab6424ed1 GetCandles
2023-05-20 16:13:17,926 DEBUG:Trying to call
2023-05-20 16:13:18,034 DEBUG:Call succeeded
2023-05-20 16:13:18,035 INFO:64689d3edded6d0d34afa85533220f79 GetCandles
2023-05-20 16:13:18,070 DEBUG:Trying to call


...

Время: 2023-05-15 10:14:00+00:00, Цена: 229 TP = 1681.0, Покупка: 20%, Продажа: 80%
Время: 2023-05-15 10:15:00+00:00, Цена: 229 TP = 270.0, Покупка: 100%, Продажа: 0%
Время: 2023-05-15 10:16:00+00:00, Цена: 229 TP = 3282.0, Покупка: 0%, Продажа: 100%
Время: 2023-05-15 10:17:00+00:00, Цена: 229 TP = 2810.0, Покупка: 13%, Продажа: 87%
Время: 2023-05-15 10:18:00+00:00, Цена: 229 TP = 2609.0, Покупка: 0%, Продажа: 100%
Время: 2023-05-15 10:19:00+00:00, Цена: 229 TP = 3870.0, Покупка: 91%, Продажа: 9%
Время: 2023-05-15 10:20:00+00:00, Цена: 229 TP = 1483.0, Покупка: 100%, Продажа: 0%
Время: 2023-05-15 10:21:00+00:00, Цена: 229 TP = 5728.0, Покупка: 0%, Продажа: 100%
Время: 2023-05-15 10:22:00+00:00, Цена: 229 TP = 4148.0, Покупка: 33%, Продажа: 67%
Время: 2023-05-15 10:23:00+00:00, Цена: 229 TP = 4931.0, Покупка: 50%, Продажа: 50%
Время: 2023-05-15 10:24:00+00:00, Цена: 229 TP = 1161.0, Покупка: 100%, Продажа: 0%
Время: 2023-05-15 10:25:00+00:00, Цена: 229 TP = 1150.0, Покупка: 67%, Продажа

2023-05-20 16:13:30,713 DEBUG:Call succeeded
2023-05-20 16:13:30,714 INFO:64689d4a868de55fec8ff24f4b86b9f4 GetCandles
2023-05-20 16:13:30,765 DEBUG:Trying to call
2023-05-20 16:13:30,861 DEBUG:Call succeeded
2023-05-20 16:13:30,861 INFO:64689d4a3447f5b6fee72acb65816baa GetCandles
2023-05-20 16:13:30,909 DEBUG:Trying to call


Время: 2023-05-17 10:14:00+00:00, Цена: 229 TP = 3711.0, Покупка: 40%, Продажа: 60%
Время: 2023-05-17 10:15:00+00:00, Цена: 229 TP = 11959.0, Покупка: 81%, Продажа: 19%
Время: 2023-05-17 10:16:00+00:00, Цена: 229 TP = 859.0, Покупка: 43%, Продажа: 57%
Время: 2023-05-17 10:17:00+00:00, Цена: 229 TP = 1479.0, Покупка: 18%, Продажа: 82%
Время: 2023-05-17 10:18:00+00:00, Цена: 229 TP = 5407.0, Покупка: 0%, Продажа: 100%
Время: 2023-05-17 10:19:00+00:00, Цена: 229 TP = 1084.0, Покупка: 0%, Продажа: 100%
Время: 2023-05-17 10:20:00+00:00, Цена: 229 TP = 2747.0, Покупка: 75%, Продажа: 25%
Время: 2023-05-17 10:21:00+00:00, Цена: 230 TP = 20549.0, Покупка: 100%, Продажа: 0%
Время: 2023-05-17 10:22:00+00:00, Цена: 229 TP = 5490.0, Покупка: 40%, Продажа: 60%
Время: 2023-05-17 10:23:00+00:00, Цена: 229 TP = 3557.0, Покупка: 100%, Продажа: 0%
Время: 2023-05-17 10:24:00+00:00, Цена: 229 TP = 1435.0, Покупка: 75%, Продажа: 25%
Время: 2023-05-17 10:25:00+00:00, Цена: 230 TP = 7218.0, Покупка: 86%, Прод

2023-05-20 16:13:31,369 DEBUG:Call succeeded
2023-05-20 16:13:31,370 INFO:64689d4b77ebc19bee37d172ce4c93a5 GetCandles


Время: 2023-05-19 10:14:00+00:00, Цена: 231 TP = 1032.0, Покупка: 15%, Продажа: 85%
Время: 2023-05-19 10:15:00+00:00, Цена: 231 TP = 1363.0, Покупка: 0%, Продажа: 100%
Время: 2023-05-19 10:16:00+00:00, Цена: 231 TP = 477.0, Покупка: 14%, Продажа: 86%
Время: 2023-05-19 10:17:00+00:00, Цена: 231 TP = 2275.0, Покупка: 10%, Продажа: 90%
Время: 2023-05-19 10:18:00+00:00, Цена: 231 TP = 1950.0, Покупка: 50%, Продажа: 50%
Время: 2023-05-19 10:19:00+00:00, Цена: 231 TP = 492.0, Покупка: 80%, Продажа: 20%
Время: 2023-05-19 10:20:00+00:00, Цена: 231 TP = 1538.0, Покупка: 31%, Продажа: 69%
Время: 2023-05-19 10:21:00+00:00, Цена: 231 TP = 1908.0, Покупка: 0%, Продажа: 100%
Время: 2023-05-19 10:22:00+00:00, Цена: 231 TP = 1870.0, Покупка: 57%, Продажа: 43%
Время: 2023-05-19 10:23:00+00:00, Цена: 231 TP = 4460.0, Покупка: 55%, Продажа: 45%
Время: 2023-05-19 10:24:00+00:00, Цена: 231 TP = 2564.0, Покупка: 22%, Продажа: 78%
Время: 2023-05-19 10:25:00+00:00, Цена: 231 TP = 1129.0, Покупка: 44%, Продажа

In [ ]:
from tinkoff.invest import Client

TOKEN = 't.b7eKSJEp3fpSiiv4mVt4fWwKIxaMHM1lDMtpGsPTeyl850b9Y4MluXYv-EQrj1vEu7QfkNwqGqGPfTW9N6EvTg'

import pandas as pd
from datetime import timedelta
from datetime import datetime, timedelta, timezone
from decimal import Decimal
from tinkoff.invest import CandleInterval, Client, HistoricCandle, Quotation, SubscriptionInterval
from tinkoff.invest.utils import now

__all__ = (
    "get_intervals",
    "quotation_to_decimal",
    "decimal_to_quotation",
    "candle_interval_to_subscription_interval",
    "now",
    "candle_interval_to_timedelta",
    "ceil_datetime",
    "floor_datetime",
    "dataclass_from_dict",
    "datetime_range_floor",
)


'''MoneyValue — используется для параметров, у которых есть денежный эквивалент. Возьмем для примера стоимость ценных бумаг — тип состоит из трех параметров:
1) currency — строковый ISO-код валюты, например RUB или USD;
2) units — целая часть суммы;
3) nano — дробная часть суммы, миллиардные доли единицы.
'''
# Quotation type = MoneyValue. We need to convert this to decimal in order to fetch price per share
def quotation_to_decimal(quotation: Quotation) -> Decimal:
    fractional = quotation.nano / Decimal("10e8")
    return Decimal(quotation.units) + fractional

def get_stock_volumes(_input: int):
    return f'{_input:,} ₽'

def get_final_float_stock_volumes(_input: int):
    return f'{_input:,} ₽'

def get_final_lots(_lots: int):
    return f'{_lots:,} шт.'

def calculate_net_change(current_closing_price: int, prev_closing_price: int):
    return f'Изменение цены: {round(((current_closing_price - prev_closing_price) / prev_closing_price * 100), 2)}%'

def calculate_net_change_per_day(current_closing_price: int, yesterday_closing_price: int):
    # current price minus 840 indexes in order to fetch price index yesterday for 1 minute candle
    return f'Изменение за день: {round(((current_closing_price - yesterday_closing_price) / yesterday_closing_price * 100), 2)}%'

def calculate_net_change_float(current_closing_price: float, prev_closing_price: float):
    return f'Изменение цены: {round(((current_closing_price - prev_closing_price) / prev_closing_price * 100), 2)}%'

def calculate_net_change_per_day_float(current_closing_price: float, yesterday_closing_price: float):
    # current price minus 840 indexes in order to fetch price index yesterday for 1 minute candle
    return f'Изменение за день: {round(((current_closing_price - yesterday_closing_price) / yesterday_closing_price * 100), 2)}%'

def make_million_volumes_on_float_stock_prices(price: int):
    price = str(price)
    price += '0000'
    return int(price)

volumes = []
prices = []
time = []


def main():
    # vtbr BBG004730ZJ9
    # lkoh BBG004731032
    # yndx BBG006L8G4H1
    with Client(TOKEN) as client:
        l1_volumes = []
        l2_lots = []
        l3_prices = []
        l4_time = []
        data = {"Объем": l1_volumes, "Лоты": l2_lots, "Цена": l3_prices, "Время": l4_time}
        threshold = 8.0
        for candle in client.get_all_candles(
            figi="BBG004731032",
            from_=now() - timedelta(days=90),
            interval=CandleInterval.CANDLE_INTERVAL_1_MIN,
        ):
            if quotation_to_decimal(candle.close) < 1:
                final_stock_volume_rub = int(candle.volume * float(quotation_to_decimal(candle.close)))
                l1_volumes.append(make_million_volumes_on_float_stock_prices(final_stock_volume_rub))
                l2_lots.append(get_final_lots(candle.volume)) # get_final_lots
                l3_prices.append(float(quotation_to_decimal(candle.close)))
                l4_time.append(candle.time)

                #print(f'ВТБ (VTBR), Время: {candle.time}, {get_final_lots(candle.volume)}, {get_final_float_stock_volumes(make_million_volumes_on_float_stock_prices(final_stock_volume_rub))}, Цена: {float(quotation_to_decimal(candle.close))} ₽')


            else:
                final_stock_volume_rub = int(candle.volume * quotation_to_decimal(candle.close))
                l1_volumes.append(final_stock_volume_rub)
                l2_lots.append(get_final_lots(candle.volume)) # get_final_lots
                l3_prices.append(int(quotation_to_decimal(candle.close)))
                l4_time.append(candle.time)
                '''l1_volumes.append(final_stock_volume_rub)
                l2_lots.append(get_final_lots(candle.volume))
                l3_prices.append(int(quotation_to_decimal(candle.close)))
                l4_time.append(candle.time)'''

                #print(f'Лукойл (LKOH), Время: {candle.time}, {get_final_lots(candle.volume)}, {get_final_stock_volumes(final_stock_volume_rub)}, Цена: {float(quotation_to_decimal(candle.close))} ₽')
        
        df = pd.DataFrame(data)

        '''Объем                 97,580,000 ₽
           Лоты                   461,947 шт.
           Цена                      0.021125
           Время    2023-04-27 07:16:00+00:00
           Name: 52227, dtype: object'''
        #print(type(df["Объем"].iloc[52227]))

        # Calculate the rolling average and standard deviation of the trading volume
        volume_mean = round(df["Объем"].mean())
        volume_std = round(df["Объем"].std())

        # Calculate the rolling average and standard deviation of the trading prices
        prcies_mean = round(df["Цена"].mean())
        prices_std = round(df["Цена"].std())

        for i in range(len(df)):
            abnormal_volume = (df['Объем'].iloc[i] - volume_mean) / volume_std
            abnormal_price_changes = (df['Цена'].iloc[i] - prcies_mean) / prices_std
            #print(abnormal_volume, abnormal_price_changes)

            if abnormal_volume > threshold or abnormal_price_changes > threshold:
                if type(df["Цена"].iloc[i]) == float:
                    print(f'Зафиксирован аномальный объем! ТГКН-14 (TGKN) {get_stock_volumes(df["Объем"].iloc[i])},  Цена: {df["Цена"].iloc[i]} ₽, {calculate_net_change_float(df["Цена"].iloc[i], df["Цена"].iloc[i - 1])}, {df["Время"].iloc[i]}, {calculate_net_change_per_day_float(df["Цена"].iloc[i], df["Цена"].iloc[i - 840])}, Время: {df["Время"].iloc[i]}')
                else:
                    print(f'Зафиксирован аномальный объем! Лукойл (LKOH) {get_stock_volumes(df["Объем"].iloc[i])},  Цена: {df["Цена"].iloc[i]} ₽, {calculate_net_change(df["Цена"].iloc[i], df["Цена"].iloc[i - 1])}, {df["Время"].iloc[i]}, {calculate_net_change_per_day(df["Цена"].iloc[i], df["Цена"].iloc[i - 840])}, Время: {df["Время"].iloc[i]}')
        
    return 0

if __name__ == "__main__":
    main()


In [ ]:
dataframe = {'Объем': volumes, 'Цена': prices, 'Время': time}
df = pd.DataFrame(dataframe)
threshold = 8.0

# Calculate the rolling average and standard deviation of the trading volume
volume_mean = df['Объем'].mean()
volume_std = df['Объем'].std()

# Calculate the rolling average and standard deviation of the trading prices
prcies_mean = df['Цена'].mean()
prices_std = df['Цена'].std()

#abnormal_volume = (df['Объем'].iloc[-1] - volume_mean) / volume_std

def calculate_net_change(current_closing_price: int, prev_closing_price: int):
    return f'Изменение цены: {round(((current_closing_price - prev_closing_price) / prev_closing_price * 100), 2)}%'

def calculate_net_change_per_day(current_closing_price: int, yesterday_closing_price: int):
    # current price minus 840 indexes in order to fetch price index yesterday for 1 minute candle
    return f'Изменение за день: {round(((current_closing_price - yesterday_closing_price) / yesterday_closing_price * 100), 2)}%'

def calculate_net_change_float(current_closing_price: float, prev_closing_price: float):
    return f'Изменение цены: {round(((current_closing_price - prev_closing_price) / prev_closing_price * 100), 2)}%'

def calculate_net_change_per_day_float(current_closing_price: float, yesterday_closing_price: float):
    # current price minus 840 indexes in order to fetch price index yesterday for 1 minute candle
    return f'Изменение за день: {round(((current_closing_price - yesterday_closing_price) / yesterday_closing_price * 100), 2)}%'

for i in range(len(df)):
    abnormal_volume = (df['Объем'].iloc[i] - volume_mean) / volume_std
    abnormal_price_changes = (df['Цена'].iloc[i] - prcies_mean) / prices_std
    #print(abnormal_volume, abnormal_price_changes)

    if abnormal_volume > threshold or abnormal_price_changes > threshold:
        if type(df["Цена"].iloc[i]) == float:
            print(f'Зафиксирован аномальный объем! ТГКН-14 (TGKN) {get_stock_volumes(df["Объем"].iloc[i])},  Цена: {df["Цена"].iloc[i]} ₽, {calculate_net_change_float(df["Цена"].iloc[i], df["Цена"].iloc[i - 1])}, {df["Время"].iloc[i]}, {calculate_net_change_per_day_float(df["Цена"].iloc[i], df["Цена"].iloc[i - 840])}, Время: {df["Время"].iloc[i]}')
        else:
            print(f'Зафиксирован аномальный объем! Лукойл (LKOH) {get_stock_volumes(df["Объем"].iloc[i])},  Цена: {df["Цена"].iloc[i]} ₽, {calculate_net_change(df["Цена"].iloc[i], df["Цена"].iloc[i - 1])}, {df["Время"].iloc[i]}, {calculate_net_change_per_day(df["Цена"].iloc[i], df["Цена"].iloc[i - 840])}, Время: {df["Время"].iloc[i]}')

In [ ]:
import asyncio
import logging
import os
from datetime import timedelta
from typing import List, Optional

from tinkoff.invest import AioRequestError, AsyncClient, CandleInterval, HistoricCandle
from tinkoff.invest.async_services import AsyncServices
from tinkoff.invest.utils import now

TOKEN = 't.b7eKSJEp3fpSiiv4mVt4fWwKIxaMHM1lDMtpGsPTeyl850b9Y4MluXYv-EQrj1vEu7QfkNwqGqGPfTW9N6EvTg'


logging.basicConfig(format="%(asctime)s %(levelname)s:%(message)s", level=logging.DEBUG)
logger = logging.getLogger(__name__)


class LogOnlyCandlesStrategy:
    """This class is responsible for a strategy. You can put here
    your methods for your strategy."""

    def __init__(
        self,
        figi: str,
        timeframe: CandleInterval,
        days_back: int,
        check_interval: int,
        client: Optional[AsyncServices],
    ):
        self.account_id = None
        self.figi = figi
        self.timeframe = timeframe
        self.days_back = days_back
        self.check_interval = check_interval
        self.client = client
        self.candles: List[HistoricCandle] = []

    async def get_historical_data(self):
        """
        Gets historical data for the instrument. Returns list of candles.
        Requests all the candles of timeframe from days_back to now.

        :return: list of HistoricCandle
        """
        logger.debug(
            "Start getting historical data for %s days back from now. figi=%s",
            self.days_back,
            self.figi,
        )
        async for candle in self.client.get_all_candles(
            figi=self.figi,
            from_=now() - timedelta(days=self.days_back),
            to=now(),
            interval=self.timeframe,
        ):
            if candle not in self.candles:
                if candle.is_complete:
                    self.candles.append(candle)
                    logger.debug("Found %s - figi=%s", candle, self.figi)

    async def ensure_market_open(self):
        """
        Ensure that the market is open. Loop until the instrument is available.
        :return: when instrument is available for trading
        """
        trading_status = await self.client.market_data.get_trading_status(
            figi=self.figi
        )
        while not (
            trading_status.market_order_available_flag
            and trading_status.api_trade_available_flag
        ):
            logger.debug("Waiting for the market to open. figi=%s", self.figi)
            await asyncio.sleep(60)
            trading_status = await self.client.market_data.get_trading_status(
                figi=self.figi
            )

    async def main_cycle(self):
        """Main cycle for live strategy."""
        while True:
            try:
                await self.ensure_market_open()
                await self.get_historical_data()

                # put your strategy code here for live
                # to generate signals for buying or selling tickers
                logger.debug(
                    "- live mode: run some strategy code to buy or sell - figi=%s",
                    self.figi,
                )

            except AioRequestError as are:
                logger.error("Client error %s", are)

            await asyncio.sleep(self.check_interval)

    async def start(self):
        """Strategy starts from this function."""
        if self.account_id is None:
            try:
                self.account_id = (
                    (await self.client.users.get_accounts()).accounts.pop().id
                )
            except AioRequestError as are:
                logger.error("Error taking account id. Stopping strategy. %s", are)
                return
        await self.main_cycle()


async def run_strategy(portfolio, timeframe, days_back, check_interval):
    """From this function we are starting
    strategy for every ticker from portfolio.
    """
    async with AsyncClient(token=TOKEN, app_name="TinkoffApp") as client:
        strategy_tasks = []
        for instrument in portfolio:
            strategy = LogOnlyCandlesStrategy(
                figi=instrument,
                timeframe=timeframe,
                days_back=days_back,
                check_interval=check_interval,
                client=client,
            )
            strategy_tasks.append(asyncio.create_task(strategy.start()))
        await asyncio.gather(*strategy_tasks)


if __name__ == "__main__":

    vtbr_figi = "BBG004730ZJ9"
    portfolio = {vtbr_figi}
    timeframe = CandleInterval.CANDLE_INTERVAL_1_MIN
    days_back = 1
    check_interval = 10  # seconds to check interval for new completed candle

    loop = asyncio.get_event_loop()
    task = loop.create_task(
        run_strategy(
            portfolio=portfolio,
            timeframe=timeframe,
            days_back=days_back,
            check_interval=check_interval,
        )
    )
    loop.run_until_complete(task)
